# Narrabeen Slope Test
With full topo and bathy combined

## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
from tqdm import tqdm_notebook
from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
from scipy import stats
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from scipy.interpolate import interp1d
from pandas.api.types import CategoricalDtype
from scipy.interpolate import UnivariateSpline
from shapely.geometry import Point, LineString

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,6)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"
plt.rcParams['axes.grid']=True

# https://stackoverflow.com/a/20709149
matplotlib.rcParams['text.usetex'] = True

matplotlib.rcParams['text.latex.preamble'] = [
       r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
       r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
       r'\usepackage{helvet}',    # set the normal font here
       r'\usepackage{amsmath}',
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
]  

## Import .csv data

In [ ]:
data_filename = '08-narr-topo-bathy-slope-test-full-profiles.csv'

df_profiles = pd.read_csv(data_filename).set_index(['site_id','x'])
df_profiles = df_profiles[~df_profiles.index.duplicated(keep='first')]
print('df_profiles:')
df_profiles.head()

In [ ]:
# Manually cut off the prestorm topo 
cuts = {'NARRA0004': {'prestorm_topo_max_x': 330,
                      'poststorm_topo_max_x': 250},
        'NARRA0008': {'prestorm_topo_max_x': 290,
                      'poststorm_topo_max_x': 250},
        'NARRA0012': {'prestorm_topo_max_x': 300,
                      'poststorm_topo_max_x': 250},
        'NARRA0016': {'prestorm_topo_max_x': 300,
                      'poststorm_topo_max_x': 225},
        'NARRA0021': {'prestorm_topo_max_x': 280,
                      'poststorm_topo_max_x': 225},
        'NARRA0023': {'prestorm_topo_max_x': 275,
                      'poststorm_topo_max_x': 215},
        'NARRA0027': {'prestorm_topo_max_x': 260,
                      'poststorm_topo_max_x': 225},
        'NARRA0031': {'prestorm_topo_max_x': 260,
                      'poststorm_topo_max_x': 225},
       }

for site_id in cuts:
    mask1 = df_profiles.index.get_level_values('site_id') == site_id
    mask2 = df_profiles.index.get_level_values('x') > cuts[site_id]['prestorm_topo_max_x']
    df_profiles.loc[(mask1)&(mask2), 'pre_topo'] = np.nan
    
    mask3 = df_profiles.index.get_level_values('x') > cuts[site_id]['poststorm_topo_max_x']
    df_profiles.loc[(mask1)&(mask3), 'post_topo'] = np.nan



In [ ]:
# for site_id,df_site in df_profiles.groupby('site_id'):
#     f, (ax1) = plt.subplots(1,1, figsize=(6, 3))
#     ax1.set_title(site_id)
    
#     ax1.plot(df_site.index.get_level_values('x'),
#              df_site.pre_topo,
#              label='Pre Topo',
#              color='#2c7bb6')
#     ax1.plot(df_site.index.get_level_values('x'),
#              df_site.pre_bathy,
#              label='Pre Bathy',
#              color='#abd9e9')

#     ax1.plot(df_site.index.get_level_values('x'),
#              df_site.post_topo,
#              label='Post Topo',
#              color='#d7191c')
#     ax1.plot(df_site.index.get_level_values('x'),
#              df_site.post_bathy,
#              label='Post Bathy',
#              color='#fdae61')

#     ax1.legend()
#     plt.show()
#     plt.close()

In [ ]:
df_profiles = df_profiles.dropna(
    subset=['post_topo', 'post_bathy', 'pre_bathy', 'pre_topo'], how='all')

df_profiles = df_profiles.reset_index()
df_profiles = df_profiles.melt(id_vars=['site_id','x','lat','lon'],
                               value_vars=['post_topo','post_bathy','pre_bathy','pre_topo']).rename(columns={'variable':'profile_type', 'value':'z'})

df_profiles = df_profiles.dropna(subset=['z'])

df_profiles.loc[df_profiles.profile_type=='post_topo','profile_type']='poststorm'
df_profiles.loc[df_profiles.profile_type=='post_bathy','profile_type']='poststorm'
df_profiles.loc[df_profiles.profile_type=='pre_topo','profile_type']='prestorm'
df_profiles.loc[df_profiles.profile_type=='pre_bathy','profile_type']='prestorm'

df_profiles = df_profiles.set_index(['site_id', 'profile_type', 'x'])
df_profiles = df_profiles[~df_profiles.index.duplicated(keep='first')]

df_profiles = df_profiles.sort_index()

print('df_profiles:')
df_profiles.head()

In [ ]:
# Just plots each site's x and z values
for site_id,df_site in df_profiles.groupby('site_id'):
    f, (ax1) = plt.subplots(1,1, figsize=(6, 3))
    ax1.set_title(site_id)
    
    prestorm=df_site.index.get_level_values('profile_type') == 'prestorm'
    ax1.plot(df_site[prestorm].index.get_level_values('x'),
             df_site[prestorm].z,
             label='Pre Topo',
             color='#2c7bb6')

    
    poststorm=df_site.index.get_level_values('profile_type') == 'poststorm'
    ax1.plot(df_site[poststorm].index.get_level_values('x'),
             df_site[poststorm].z,
             label='Post Topo',
             color='#d7191c')


    ax1.legend()
    plt.show()
    plt.close()

## Get dune faces

In [ ]:
# Manually define dune x coordinates and work out slope

dune_data = [
    {
        'site_id': 'NARRA0004',
        'dune_crest_x': 180,
        'dune_toe_x': 205
    },
    {
        'site_id': 'NARRA0008',
        'dune_crest_x': 180,
        'dune_toe_x': 205
    },
    {
        'site_id': 'NARRA0012',
        'dune_crest_x': 195,
        'dune_toe_x': 205
    },
    {
        'site_id': 'NARRA0016',
        'dune_crest_x': 190,
        'dune_toe_x': 200
    },
    {
        'site_id': 'NARRA0021',
        'dune_crest_x': 205,
        'dune_toe_x': 210
    },
    {
        'site_id': 'NARRA0023',
        'dune_crest_x': 205,
        'dune_toe_x': 215
    },
    {
        'site_id': 'NARRA0027',
        'dune_crest_x': 210,
        'dune_toe_x': 219
    },
    {
        'site_id': 'NARRA0031',
        'dune_crest_x': 210,
        'dune_toe_x': 218
    },
]

for site_dune in dune_data:
    df_site = df_profiles.xs(site_dune['site_id'], level='site_id').xs('prestorm',level='profile_type')
    
    dune_crest_x = site_dune['dune_crest_x']
    dune_toe_x = site_dune['dune_toe_x']
    dune_crest_z = df_site.iloc[df_site.index.get_loc(site_dune['dune_crest_x'],method='nearest')].z
    dune_toe_z = df_site.iloc[df_site.index.get_loc(site_dune['dune_toe_x'],method='nearest')].z

    dune_slope = (dune_crest_z - dune_toe_z)/(dune_crest_x - dune_toe_x)
    
    site_dune['dune_crest_z'] = dune_crest_z
    site_dune['dune_toe_z'] = dune_toe_z
    site_dune['dune_slope'] = dune_slope
    
    
# Join back into main data
df_dunes = pd.DataFrame(dune_data).set_index('site_id')
print('df_dunes:')
df_dunes.head()

In [ ]:
# # Just plots each site's x and z values
# for site_id,df_site in df_profiles.xs('prestorm',level='profile_type').groupby('site_id'):
#     f, (ax1) = plt.subplots(1,1, figsize=(6, 3))
#     ax1.set_title(site_id)
#     ax1.plot(df_site.index.get_level_values('x'),
#              df_site.z)
#     ax1.plot([df_dunes.loc[site_id].dune_crest_x, df_dunes.loc[site_id].dune_toe_x],
#              [df_dunes.loc[site_id].dune_crest_z, df_dunes.loc[site_id].dune_toe_z],
#             'r.-')
#     ax1.set_xlim([150,250])
#     ax1.set_ylim([0,15])
#     plt.show()
#     plt.close()

## Get prestorm slope

In [ ]:
z_ele = 0.7
debug=False

def find_nearest_idx(array, value):
    array = np.asarray(array)
    idx = (np.abs(array - value)).argmin()
    return idx

prestorm_slope_data =[]
for site_id, df_site in df_profiles.xs('prestorm',level='profile_type').groupby('site_id'):
    
    # Find index of our z_ele
    idx = np.where(df_site.z.values>=z_ele)[0][-1]
    
    prestorm_end_x = df_site.iloc[idx].name[1]
    prestorm_end_z = df_site.iloc[idx].z
    
    prestorm_start_x = df_dunes.loc[site_id].dune_toe_x
    prestorm_start_z = df_dunes.loc[site_id].dune_toe_z
    
    prestorm_slope = (prestorm_end_z-prestorm_start_z)/(prestorm_end_x-prestorm_start_x)
    
    prestorm_slope_data.append({
        'site_id': site_id,
        'prestorm_end_x': prestorm_end_x,
        'prestorm_end_z': prestorm_end_z,
        'prestorm_start_x': prestorm_start_x,
        'prestorm_start_z': prestorm_start_z,
        'prestorm_slope': prestorm_slope
    })
    
df_prestorm_slope = pd.DataFrame(prestorm_slope_data).set_index(['site_id'])
print('df_prestorm_slope:')
df_prestorm_slope.head()
    

## Get shelf slope
At 10 m contour

In [ ]:
# Elevation to take shelf slope at
z_ele = -9
debug=False

def find_nearest_idx(array, value):
    array = np.asarray(array)
    idx = (np.abs(array - value)).argmin()
    return idx

def slope_at_point(x, z, z_ele,debug=False):
    # Smooth profile a bit
    # TODO the smoothing factor will change based on the number of data points
    # Need to fix
    s = UnivariateSpline(x, z, s=50)
    xs = np.linspace(min(x),max(x),1000)
    zs = s(xs)

    # Calculate derivates of spline
    dzdx = np.diff(zs)/np.diff(xs)

    # Find index of z_ele
    idx = find_nearest_idx(zs, z_ele)
    slope = dzdx[idx]
    shelf_x = xs[idx]


    
    # For checking how much smoothing is going on
    if debug:
        f, (ax1) = plt.subplots(1,1, figsize=(6, 3))
        ax1.plot(x,z)
        ax1.plot(xs,zs)
        plt.show()
        plt.close()
    
    return slope, shelf_x, z_ele
    
shelf_data = []
for site_id, df_site in df_profiles.xs('prestorm',level='profile_type').groupby('site_id'):
    shelf_slope, shelf_x, shelf_z = slope_at_point(df_site.index.get_level_values('x').values,
                                 df_site.z, 
                                 z_ele, debug=debug)
    shelf_data.append({
        'site_id': site_id,
        'shelf_slope': shelf_slope,
        'shelf_x': shelf_x,
        'shelf_z': shelf_z
    })
    
df_shelf = pd.DataFrame(shelf_data).set_index(['site_id'])

df_shelf.loc['NARRA0004','shelf_slope'] = -0.02

print('df_shelf:')
df_shelf.head()

## Do geometry


df_site

In [ ]:
for site_id, df_site in df_profiles.groupby('site_id'):

    # Project the dune face outwards
    dune_face_toe = Point(df_dunes.loc[site_id].dune_toe_x,
                          df_dunes.loc[site_id].dune_toe_z)
    dune_face_sea = Point(
        df_dunes.loc[site_id].dune_toe_x + 1000,
        #         df_dunes.loc[site_id].dune_toe_z +1000 * -1
        df_dunes.loc[site_id].dune_toe_z +
        1000 * df_dunes.loc[site_id].dune_slope)
    dune_line = LineString([dune_face_toe, dune_face_sea])

    # Project the shelf slope landwards
    shelf_point = Point(df_shelf.loc[site_id].shelf_x,
                        df_shelf.loc[site_id].shelf_z)
    shelf_land = Point(
        df_shelf.loc[site_id].shelf_x - 1000, df_shelf.loc[site_id].shelf_z -
        1000 * df_shelf.loc[site_id].shelf_slope)
    shelf_sea = Point(
        df_shelf.loc[site_id].shelf_x + 1000, df_shelf.loc[site_id].shelf_z +
        1000 * df_shelf.loc[site_id].shelf_slope)
    shelf_line = LineString([shelf_land, shelf_point, shelf_sea])

    # Find intersection between to lines
    dune_shelf_int = dune_line.intersection(shelf_line)
    dist_toe_to_int = dune_face_toe.distance(dune_shelf_int)

    # Plots
    f, (ax1) = plt.subplots(1, 1, figsize=(12, 4))

    # Raw profile prestorm
    ax1.plot(
        df_site.xs('prestorm',
                   level='profile_type').index.get_level_values('x'),
        df_site.xs('prestorm', level='profile_type').z,
        label='Prestorm profile')

    # Raw profile poststorm
    ax1.plot(
        df_site.xs('poststorm',
                   level='profile_type').index.get_level_values('x'),
        df_site.xs('poststorm', level='profile_type').z,
        label='Poststorm profile')

    # Dune face
    ax1.plot(
        [df_dunes.loc[site_id].dune_crest_x, df_dunes.loc[site_id].dune_toe_x],
        [df_dunes.loc[site_id].dune_crest_z, df_dunes.loc[site_id].dune_toe_z],
        linestyle=':',
        color='#999999',
        label='Dune face ({:.2f})'.format(-df_dunes.loc[site_id].dune_slope))

    # Projected dune face
    ax1.plot(
        dune_line.xy[0],
        dune_line.xy[1],
        linestyle='--',
        color='#999999',
        label='Dune face (projected)')

    # Projected shelf slope
    ax1.plot(
        shelf_line.xy[0],
        shelf_line.xy[1],
        linestyle='--',
        color='#999999',
        label='Shelf slope (projected)')

    # Intersection
    ax1.scatter(
        dune_shelf_int.xy[0],
        dune_shelf_int.xy[1],
        marker='x',
        color='#999999',
        label='Dune/shelf projected intersection')

    # Prestorm slope
    ax1.plot([
        df_prestorm_slope.loc[site_id].prestorm_start_x,
        df_prestorm_slope.loc[site_id].prestorm_end_x
    ], [
        df_prestorm_slope.loc[site_id].prestorm_start_z,
        df_prestorm_slope.loc[site_id].prestorm_end_z
    ],
             color='violet',
             label='Prestorm slope ({:.2f})'.format(
                 -df_prestorm_slope.loc[site_id].prestorm_slope))

    #     # Find best slope based on distance form toe to intersection?
    #     best_slope_toe = shelf_line.interpolate(
    #         shelf_line.project(intersection) - 4 * dist_toe_to_int)
    #     best_slope = (dune_face_toe.xy[1][0] - best_slope_toe.xy[1][0]) / (
    #         dune_face_toe.xy[0][0] - best_slope_toe.xy[0][0])

    #     # Best slope toe
    #     ax1.scatter(
    #         best_slope_toe.xy[0], best_slope_toe.xy[1], marker='o', color='g')

    #     # Best slope
    #     ax1.plot([dune_face_toe.xy[0], best_slope_toe.xy[0]],
    #              [dune_face_toe.xy[1], best_slope_toe.xy[1]],
    #              color='g',
    #              label='Best slope ({:.3f})'.format(-best_slope))

    # Find best slope based on intersection of prestorm slope and surf zone slope
    prestorm_slope_line = LineString([
        Point(
            df_prestorm_slope.loc[site_id].prestorm_start_x,
            df_prestorm_slope.loc[site_id].prestorm_start_z,
        ),
        Point(
            df_prestorm_slope.loc[site_id].prestorm_start_x + 10000,
            df_prestorm_slope.loc[site_id].prestorm_start_z +
            10000 * df_prestorm_slope.loc[site_id].prestorm_slope)
    ])

    # Where prestorm slope projection intersects shelf line
    prestorm_slope_shelf_int = prestorm_slope_line.intersection(shelf_line)

    # Distance between dune/shelf intersection and prestorm/shelf intersection
    dist_shelf_prestorm_ints = prestorm_slope_shelf_int.distance(
        dune_shelf_int)

    best_slope_pt = shelf_line.interpolate(
        shelf_line.project(dune_shelf_int) + 0.3 * (shelf_line.project(prestorm_slope_shelf_int) -
               shelf_line.project(dune_shelf_int)))
    
    best_slope =(df_prestorm_slope.loc[site_id].prestorm_start_z-best_slope_pt.xy[1][0])/(df_prestorm_slope.loc[site_id].prestorm_start_x-best_slope_pt.xy[0][0])
    
    if not prestorm_slope_shelf_int.is_empty:
        ax1.plot(
            prestorm_slope_shelf_int.xy[0],
            prestorm_slope_shelf_int.xy[1],
            marker='x',
            color='#999999',
            label='Prestorm slope/shelf\nprojected intersection')
        ax1.plot(
            prestorm_slope_line.xy[0],
            prestorm_slope_line.xy[1],
            color='#999999',
            linestyle='--',
            label='Prestorm slope projected line')
        ax1.plot(
            [df_prestorm_slope.loc[site_id].prestorm_start_x,
             best_slope_pt.xy[0][0]],
            [df_prestorm_slope.loc[site_id].prestorm_start_z,
             best_slope_pt.xy[1][0]],
            color='red',
            linestyle='--',
            label='Best slope ({:.3f})'.format(-best_slope))
        
    # TEMP Target slopes
    target_slopes = {
        'NARRA0004': 0.076,
        'NARRA0008': 0.093,
        'NARRA0012': 0.060,
        'NARRA0016': 0.11,
        'NARRA0021': 0.063,
        'NARRA0023': 0.061,
        'NARRA0027': 0.060,
        'NARRA0031': 0.057,
    }

    target_direction = {
        'NARRA0004': "flatter",
        'NARRA0008': "steeper",
        'NARRA0012': "flatter",
        'NARRA0016': "flatter",
        'NARRA0021': "steeper",
        'NARRA0023': "steeper",
        'NARRA0027': "steeper",
        'NARRA0031': "steeper",
    }
    ax1.plot([dune_face_toe.xy[0][0], dune_face_toe.xy[0][0] + 1000], [
        dune_face_toe.xy[1][0],
        dune_face_toe.xy[1][0] - 1000 * target_slopes[site_id]
    ],
             color='red',
             label='Target slope\n({} than {:.3f})'.format(
                 target_direction[site_id], target_slopes[site_id]))

    ax1.set_xlim([100, 800])
    ax1.set_ylim([-15, 12])
#     ax1.set_xlim([100, 600])
#     ax1.set_ylim([-10, 12])

    #     ax1.set_xlim([df_dunes.loc[site_id].dune_crest_x - 50,
    #                   intersection.xy[0][0] + 50])
    #     ax1.set_ylim([intersection.xy[1][0] -3,
    #                   df_dunes.loc[site_id].dune_crest_z + 3])

    ax1.set_title(site_id)
    ax1.legend(loc='upper right', prop={'size': 10})
    f.savefig('08-{}.png'.format(site_id), dpi=600)
    plt.show()
    plt.close()

In [ ]:
dune_shelf_int